# Object Retrieval API
https://v2.sherpa.ac.uk/api/object-retrieval.html

In [2]:
# APIキーを.env に格納
from dotenv import load_dotenv
load_dotenv()
api_key = os.environ['api_key']
# print(api_key)
# data = [] # 初期化
data = list(range(7))  

In [34]:
# sherpaのAPIにクエリを投げる
import requests
import json
import pprint
# https://v2.sherpa.ac.uk/cgi/retrieve?item-type=repository&api-key=<YOUR-API-KEY>&format=Json&filter=[[%22country%22,%22equals%22,%22jp%22]]
url = 'https://v2.sherpa.ac.uk/cgi/retrieve'
filterparam = '[[%22country%22,%22equals%22,%22jp%22]]'
# apiの制限は1回100件なので、offsetで調整
params = {'item-type':'repository','api-key':api_key,'format':'Json','filter':filterparam, 'offset':'700'}
# python requests クエリストリングを encodeしないようにする
params_str = "&".join("%s=%s" % (k,v) for k,v in params.items())
res = requests.get(url, params=params_str)
# print(res.url)
data[7] = json.loads(res.text)
# pprint.pprint(data)
# about 6.4s/100ken

IndexError: list assignment index out of range

In [36]:
len(data)
concat_data = {}
# 上書きされる
#concat_data.update(data[0])
#concat_data.update(data[1]) 
#concat_data = {**data[0],**data[1]}
# for mylist in range(len(data)):
#    print(mylist)
#    #concat_data.update(data[mylist])
concat_data['items'] = data[0]['items'] + data[1]['items']+ data[2]['items']+ data[3]['items']+ data[4]['items']+ data[5]['items']+ data[6]['items']

In [37]:
concat_data['items'][599]

{'repository_metadata': {'url': 'https://ncn.repo.nii.ac.jp/',
  'type_phrases': [{'value': 'institutional',
    'phrase': 'Institutional',
    'language': 'en'}],
  'oai_url': 'http://ncn.repo.nii.ac.jp/oai',
  'type': 'institutional',
  'name': [{'name': 'Nagano College of Nursing Repository',
    'preferred': 'name',
    'language': 'en',
    'preferred_phrases': [{'language': 'en',
      'value': 'name',
      'phrase': 'Name'}],
    'language_phrases': [{'phrase': 'English',
      'value': 'en',
      'language': 'en'}]},
   {'language_phrases': [{'language': 'en',
      'phrase': 'Japanese',
      'value': 'ja'}],
    'preferred_phrases': [{'language': 'en',
      'value': 'name',
      'phrase': 'Name'}],
    'language': 'ja',
    'name': '長野県看護大学リポジトリ',
    'preferred': 'name'}],
  'software': {'name': 'weko',
   'name_phrases': [{'language': 'en', 'phrase': 'WEKO', 'value': 'weko'}]}},
 'organisation': {'name': [{'preferred': 'name',
    'name': 'NAGANO COLLEGE of NURSING',
  

In [7]:
# concat_data["items"][1] の　[0],[1],... がそれぞれ1機関
# content = concat_data["items"][99]
content = concat_data['items'][99]
print(content)

{'repository_metadata': {'type': 'institutional', 'url': 'http://s-ir.sap.hokkyodai.ac.jp/', 'content_subjects': ['social_sciences'], 'name': [{'preferred': 'name', 'preferred_phrases': [{'language': 'en', 'phrase': 'Name', 'value': 'name'}], 'language_phrases': [{'value': 'en', 'phrase': 'English', 'language': 'en'}], 'name': 'Hokkaido University of Education Repository', 'language': 'en'}, {'name': '北海道教育大学学術リポジトリ', 'language_phrases': [{'value': 'ja', 'language': 'en', 'phrase': 'Japanese'}], 'language': 'ja', 'preferred': 'name', 'preferred_phrases': [{'phrase': 'Name', 'language': 'en', 'value': 'name'}]}], 'content_types_phrases': [{'value': 'journal_articles', 'language': 'en', 'phrase': 'Journal Articles'}, {'phrase': 'Reports and Working Papers', 'language': 'en', 'value': 'unpub_reports_and_working_papers'}, {'language': 'en', 'phrase': 'Other Special Item Types', 'value': 'other_special_item_types'}], 'type_phrases': [{'value': 'institutional', 'language': 'en', 'phrase': 'I

In [38]:
# len(concat_data)
len(concat_data['items'])
# concat_data

681

In [40]:
def flatten(d,sep="_"):
    import collections
    obj = collections.OrderedDict()
    def recurse(t,parent_key=""):
        if isinstance(t,list):
            for i in range(len(t)):
                recurse(t[i],parent_key + sep + str(i) if parent_key else str(i))
        elif isinstance(t,dict):
            for k,v in t.items():
                recurse(v,parent_key + sep + k if parent_key else k)
        else:
            obj[parent_key] = t
    recurse(d)
    return obj

flat_data = {}
for org in range(len(concat_data['items'])):
    flat_data[org] = flatten(concat_data['items'][org]) 

In [41]:
# print(data2.keys())
flat_data

{0: OrderedDict([('organisation_country', 'jp'),
              ('organisation_country_phrases_0_value', 'jp'),
              ('organisation_country_phrases_0_language', 'en'),
              ('organisation_country_phrases_0_phrase', 'Japan'),
              ('organisation_name_0_preferred_phrases_0_value', 'name'),
              ('organisation_name_0_preferred_phrases_0_phrase', 'Name'),
              ('organisation_name_0_preferred_phrases_0_language', 'en'),
              ('organisation_name_0_preferred', 'name'),
              ('organisation_name_0_language', 'en'),
              ('organisation_name_0_language_phrases_0_language', 'en'),
              ('organisation_name_0_language_phrases_0_phrase', 'English'),
              ('organisation_name_0_language_phrases_0_value', 'en'),
              ('organisation_name_0_name', 'Chiba University'),
              ('organisation_name_1_preferred', 'name'),
              ('organisation_name_1_preferred_phrases_0_value', 'name'),
             

In [42]:
# Pandas Dataframe でキーを列に、値を行の値に変換するには、辞書を角括弧で囲むだけ
# 完全に一列フラットになってしまう
import pandas as pd
# repometa3 = pd.DataFrame([data2[0]])
# len(data2)
repometa = pd.DataFrame(index=[], columns=[])
for org in range(len(concat_data['items'])):
    repometa = pd.concat([repometa, pd.DataFrame([flat_data[org]])])
repometa

organisation_country organisation_country_phrases_0_value  \
0                    jp                                   jp   
0                    jp                                   jp   
0                    jp                                   jp   
0                    jp                                   jp   
0                    jp                                   jp   
..                  ...                                  ...   
0                    jp                                   jp   
0                    jp                                   jp   
0                    jp                                   jp   
0                    jp                                   jp   
0                    jp                                   jp   

   organisation_country_phrases_0_language  \
0                                       en   
0                                       en   
0                                       en   
0                                       en   
0                                       en   
..                                     ...   
0                                       en   
0                                       en   
0                                       en   
0                                       en   
0                                       en   

   organisation_country_phrases_0_phrase  \
0                                  Japan   
0                                  Japan   
0                                  Japan   
0                                  Japan   
0                                  Japan   
..                                   ...   
0                                  Japan   
0                                  Japan   
0                                  Japan   
0                                  Japan   
0                                  Japan   

   organisation_name_0_preferred_phrases_0_value  \
0                                           name   
0                                           name   
0                                           name   
0                                           name   
0                                           name   
..                                           ...   
0                                           name   
0                                           name   
0                                           name   
0                                           name   
0                                           name   

   organisation_name_0_preferred_phrases_0_phrase  \
0                                            Name   
0                                            Name   
0                                            Name   
0                                            Name   
0                                            Name   
..                                            ...   
0                                            Name   
0                                            Name   
0                                            Name   
0                                            Name   
0                                            Name   

   organisation_name_0_preferred_phrases_0_language  \
0                                                en   
0                                                en   
0                                                en   
0                                                en   
0                                                en   
..                                              ...   
0                                                en   
0                                                en   
0                                                en   
0                                                en   
0                                                en   

   organisation_name_0_preferred organisation_name_0_language  \
0                           name                           en   
0                           name                           en   
0                           name  

In [43]:
# id で index をリセットする
repometa.set_index('system_metadata_id', drop=False, inplace=True)

In [44]:
repometa
# repometa.columns
# repometa['organisation_name_1_name']
# print(repometa.iloc[97:,])

organisation_country organisation_country_phrases_0_value  \
system_metadata_id                                                             
72                                   jp                                   jp   
117                                  jp                                   jp   
172                                  jp                                   jp   
484                                  jp                                   jp   
510                                  jp                                   jp   
...                                 ...                                  ...   
9913                                 jp                                   jp   
9914                                 jp                                   jp   
9915                                 jp                                   jp   
9916                                 jp                                   jp   
9917                                 jp                                   jp   

                   organisation_country_phrases_0_language  \
system_metadata_id                                           
72                                                      en   
117                                                     en   
172                                                     en   
484                                                     en   
510                                                     en   
...                                                    ...   
9913                                                    en   
9914                                                    en   
9915                                                    en   
9916                                                    en   
9917                                                    en   

                   organisation_country_phrases_0_phrase  \
system_metadata_id                                         
72                                                 Japan   
117                                                Japan   
172                                                Japan   
484                                                Japan   
510                                                Japan   
...                                                  ...   
9913                                               Japan   
9914                                               Japan   
9915                                               Japan   
9916                                               Japan   
9917                                               Japan   

                   organisation_name_0_preferred_phrases_0_value  \
system_metadata_id                                                 
72                                                          name   
117                                                         name   
172                                                         name   
484                                                         name   
510                                                         name   
...                                                          ...   
9913                                                        name   
9914                                                        name   
9915                                                        name   
9916                                                        name   
9917                                                        name   

                   organisation_name_0_preferred_phrases_0_phrase  \
system_metadata_id                                                  
72                                                           Name   
117                                                          Name   
172                                                          Name   
484                                                          Name   
510                                                          Name   
...                   

In [45]:
# エクセルファイルに出力（日付をシート名にセット）
import datetime
d_today = datetime.date.today()
repometa.to_excel('./opendoar_repository_list.xlsx', sheet_name=str(d_today))